In [205]:
df = pd.read_csv('most-watched-broadcasts.csv')[:23]
df.columns = [x.replace(' ','_').lower().replace('(','').replace(')','') for x in df.columns]
df.head()


text_index  index  rank               broadcast              broadcast_logo   
0         a1      1     1  Apollo 11 Moon landing        other-logos/moon.png  \
1         a2      2     2         Super Bowl LVII    superbowl-logos/lvii.png   
2         a3      3     3         Super Bowl XLIX    superbowl-logos/xlix.png   
3         a4      4     4          Super Bowl LVI     superbowl-logos/lvi.png   
4         a5      5     5       Super Bowl XLVIII  superbowl-logos/xlviii.png   

   average_viewers_in_millions       date   network   
0                        142.5  7/20/1969  multiple  \
1                        115.1  2/12/2023       Fox   
2                        114.4   2/1/2015       NBC   
3                        112.3  2/13/2022       NBC   
4                        112.2   2/2/2014       Fox   

                 network_logo  
0  network-logos/multiple.png  
1       network-logos/fox.png  
2       network-logos/nbc.png  
3       network-logos/nbc.png  
4       network-logos/fox.png

In [183]:
np.full(len(df),1)

array([1, 1, 1, 1, 1, 1, 1, 1, 1, 1, 1, 1, 1, 1, 1, 1, 1, 1, 1, 1, 1, 1,
       1])

In [62]:
import plotly.graph_objects as go
import plotly.express as px
from PIL import Image
import pandas as pd
import numpy as np

df = pd.read_csv('most-watched-broadcasts.csv')[:23]
df.columns = [x.replace(' ','_').lower().replace('(','').replace(')','') for x in df.columns]
df.head()


# Sample data
data = {
    'Category': df.text_index.tolist(),
    'Broadcast': df.broadcast.tolist(),
    'Network': df.network.tolist(),
    'Date': df.date.tolist(),
    'Rank': df['rank'].tolist(),
    'Value': df.average_viewers_in_millions.tolist(),
    'Logo1': df.broadcast_logo.tolist(),
    'Logo2': df.network_logo.tolist()
}

df = pd.DataFrame(data)

def is_bowl(x, return_if_true = "#B22222", return_if_false = "#775E7D"):
    x = x.lower()
    if('super bowl' in x and 'jackson' not in x):
        return  return_if_true
    else:
        return return_if_false

# Create the bar chart
fig = px.bar(df, x='Value', y='Category', color='Category', orientation='h').update_traces(width = 0.55)

# Overlay scatter plots for logos at the beginning and end of each bar
counter = 0
for b, r in zip(fig.data, df.to_dict(orient='records')):
    print(b.x)
    size_offset = -2
    png = r['Logo1']
    png2 = r['Logo2']
    broad = r['Broadcast']
    date = r['Date'].split('/')[-1] # get year
    rank = int(r['Rank'])
    value = b.x[0]
    bar_color = is_bowl(broad)
    end_logo_xanchor = 'center'
    b['showlegend'] = True if 0 < counter < 3 else False
    counter += 1
    if 'day' in png or 'roots' in png or 'mash' in png:
        size_offset = 10
    
    size_offset2 = 0
    if 'multiple' in png2:
        size_offset2 = -3

    # current super bowl
    if '/lviii.png' in png:
        rank = '?'
        value = '?'
        bar_color = 'rgba(0,0,0,0)'
        end_logo_xanchor = 'left'

        # add textured, dashed bar
        fig.add_shape(type="rect", xref="x", yref="paper",
            x0=0, y0=0.935,
            x1=b.x[0], y1=0.965,
            line=dict(color="#FED241", dash="dash", width=2),
            showlegend=False
        )
        b.marker['pattern_shape'] = '/'

    # bar color
    b.marker['color'] = bar_color

    # trace and legend name 
    b['name'] = is_bowl(broad.lower(), 'Super Bowl 🏈', 'Non Footbal 📺')
    b['legendgroup'] = is_bowl(broad.lower(), 'Football','Non Football')

    # tooltip
    b['hovertemplate'] = f'''<span style = 'text-shadow: 1px 1px 2px black'><b style='text-decoration-line: underline;'>{broad}</b>
        <br> <b>Average Viewers</b>: {value} million (rank {rank})
        <br> <b>Network</b>: {r['Network']}
        <br> <b>Date</b>: {r['Date']}
        </span>
    '''
    
    # end of bar
    fig.add_layout_image(
        x=b.x[0]+3,
        y=b.y[0],
        source=Image.open(png),
        xref="x",
        yref="y",
        sizex=13+size_offset,
        sizey=13+size_offset,
        xanchor=end_logo_xanchor,
        yanchor="middle",
    )

    # beginning of bar
    fig.add_layout_image(
        x=-6.5,
        y=b.y[0],
        source=Image.open(png2),
        xref="x",
        yref="y",
        sizex=7 + size_offset2,
        sizey=7 + size_offset2,
        xanchor="center",
        yanchor="middle"
    )

    # bar description
    fig.add_scatter(
        x=[5],
        y=[b.y[0]],
        mode = 'text',
        text = f'<span style="text-shadow: 1px 1px 2px black">{rank}. {broad} ({date})</span>',
        textfont = dict(color='white'),
        textposition='middle right',
        hovertemplate=None,
        showlegend=False
    )

    # bar value
    fig.add_scatter(
        x=[b.x[0]-10],
        y=[b.y[0]],
        mode = 'text',
        text = f'{value} mil' if 'moon' not in png else '~125 - 150 mil',
        textfont = dict(color='white'),
        textposition='middle left',
        hovertemplate=None,
        showlegend=False
    )

# Update layout
fig.update_layout(autosize=False, width=1200, height=1200, showlegend=True, template='plotly_dark',
    title=dict(text="Most Watched 📺 Broadcasts in the US <br><sup>by number of average viewers</sup>", font=dict(size=30), x = 0.5, xanchor = 'center'),
    font_size = 12,
    margin = dict(t=115),
    legend=dict(
        orientation = "h",
        title = None,
        x=0.48,
        y=1.03,
        traceorder="normal",
        xanchor = 'center',
        xref='paper'
    ),
    hoverlabel=dict(
        # bgcolor="white",
        font_size=16,
        font_family="Rockwell"
    )
)

# update axes
fig.update_xaxes(range=[-15, max(df.Value)+20], showgrid=False, title = None)
fig.update_yaxes(showticklabels = False, showgrid=False, title = None)

# add annotation
fig.add_annotation(dict(font=dict(color='white',size=15),
                                        x=0,
                                        y=-0.07,
                                        showarrow=False,
                                        text="<br>* - multiple networks<br><a href='https://en.wikipedia.org/wiki/List_of_most_watched_television_broadcasts_in_the_United_States' target='_blank'> <i>Source: List of Most Watched Broadcasts in the US<i></a>",
                                        textangle=0,
                                        align = 'left',
                                        xanchor='left',
                                        xref="paper",
                                        yref="paper"))

# add author
fig.add_annotation(dict(font=dict(color='white',size=15),
                                        x=0.85,
                                        y=-0.07,
                                        showarrow=False,
                                        text="Made with ❤️ by <a href='https://kobakhit.com/' target='_blank'>Koba K</a>",
                                        textangle=0,
                                        align = 'left',
                                        xanchor='left',
                                        xref="paper",
                                        yref="paper"))



# Show plot
fig.show()

[70.]
[142.5]
[115.1]
[114.4]
[112.3]
[112.2]
[111.9]
[111.3]
[111.3]
[111.]
[110.]
[108.7]
[106.5]
[105.9]
[103.4]
[102.]
[100.4]
[100.]
[100.]
[98.7]
[98.2]
[97.4]
[95.]


In [43]:
fig.data


(Bar({
     'alignmentgroup': 'True',
     'hovertemplate': ("<span style = 'text-shadow: 1p" ... '2/11/2024\n        </span>\n    '),
     'legendgroup': 'Football',
     'marker': {'color': 'rgba(0,0,0,0)', 'pattern': {'shape': '/'}},
     'name': 'Football',
     'offsetgroup': 'a0',
     'orientation': 'h',
     'showlegend': True,
     'textposition': 'auto',
     'width': 0.55,
     'x': array([70.]),
     'xaxis': 'x',
     'y': array(['a0'], dtype=object),
     'yaxis': 'y'
 }),
 Bar({
     'alignmentgroup': 'True',
     'hovertemplate': ("<span style = 'text-shadow: 1p" ... '7/20/1969\n        </span>\n    '),
     'legendgroup': 'Non Football',
     'marker': {'color': '#775E7D', 'pattern': {'shape': ''}},
     'name': 'Non Football',
     'offsetgroup': 'a1',
     'orientation': 'h',
     'showlegend': True,
     'textposition': 'auto',
     'width': 0.55,
     'x': array([142.5]),
     'xaxis': 'x',
     'y': array(['a1'], dtype=object),
     'yaxis': 'y'
 }),
 Bar({
     '

In [34]:
fig.write_html('most-watched-broadcasts-us-dark.html')